# Apprendre à manipuler sqlite pour gerer les notes

Références:
 - http://www.saltycrane.com/blog/2007/11/python-sqlite-tutorial-relational/
 - https://pymotw.com/2/sqlite3/
 - http://pythoncentral.io/introduction-to-sqlite-in-python/
 - http://www.datacarpentry.org/python-ecology/08-working-with-sql
 - (pour aller plus loin) https://plot.ly/python/big-data-analytics-with-pandas-and-sqlite/

# Connection à la base de données

In [7]:
import sqlite3
conn = sqlite3.connect('notes.db')
c = conn.cursor()

# Création de la base de donnée

In [21]:
c.execute('''drop table eleve''')
c.execute('''create table eleve (
id integer primary key autoincrement not null,
name text,
surname text, 
classe text
commentaire text
)''')

In [34]:
c.execute('''drop table devoir''')
c.execute('''create table devoir (
id integer primary key autoincrement not null,
name text, 
date date,
trimestre integer,
bareme integer
)''')

In [6]:
c.execute('''create table note(
id integer primary key autoincrement not null,
valeur float,
eleve_id integer not null references eleve(id),
devoir_id integer not null references devoir(id)
)''')

# Import des notes pour les 309

In [2]:
import pandas as pd
all_notes = pd.ExcelFile("309.xlsx")
notes = all_notes.parse('notes')

## Les élèves

In [3]:
eleves = notes.columns[1:31]

In [22]:
for e in eleves:
    conn.execute('''insert into eleve (name, classe) values (?, ?)''', (e,'309'))
conn.commit()

## Les notes du trimestre 1

In [46]:
devoir_t1 = notes.iloc[1:5].index
devoir_t1

Index(['DM_15_09_18', 'DS_15_09_25', 'BB_15_10_31', 'Conn trimestre 1'], dtype='object')

In [8]:
for d in devoir_t1:
    conn.execute('''insert into devoir (name, trimestre, bareme ) values (?,?,?)''', (d, 1, notes.BAREME[d]))
conn.commit()

In [42]:
for e in eleves:
    c.execute('''select id from eleve where name=?''', (e,))
    e_id = c.fetchone()[0]
    for d in devoir_t1:
        c.execute('''select id from devoir where name=?''', (d,))
        d_id = c.fetchone()[0]
        conn.execute('''insert into note (valeur, eleve_id, devoir_id) values (?,?,?)''', (notes[e][d], e_id, d_id))
conn.commit()

1 1
1 2
1 3
1 4
2 1
2 2
2 3
2 4
3 1
3 2
3 3
3 4
4 1
4 2
4 3
4 4
5 1
5 2
5 3
5 4
6 1
6 2
6 3
6 4
7 1
7 2
7 3
7 4
8 1
8 2
8 3
8 4
9 1
9 2
9 3
9 4
10 1
10 2
10 3
10 4
11 1
11 2
11 3
11 4
12 1
12 2
12 3
12 4
13 1
13 2
13 3
13 4
14 1
14 2
14 3
14 4
15 1
15 2
15 3
15 4
16 1
16 2
16 3
16 4
17 1
17 2
17 3
17 4
18 1
18 2
18 3
18 4
19 1
19 2
19 3
19 4
20 1
20 2
20 3
20 4
21 1
21 2
21 3
21 4
22 1
22 2
22 3
22 4
23 1
23 2
23 3
23 4
24 1
24 2
24 3
24 4
25 1
25 2
25 3
25 4
26 1
26 2
26 3
26 4
27 1
27 2
27 3
27 4
28 1
28 2
28 3
28 4
29 1
29 2
29 3
29 4
30 1
30 2
30 3
30 4


## Les notes du trimestre 2

In [45]:
devoir_t2 = notes.iloc[7:14].index
devoir_t2

Index(['DS_15_11_27', 'DM_15_12_09', 'Boulettes', 'BB_16_01_23', 'DM_16_01_29',
       'Brevet blanc Fevrier', 'Conn trimestre 2'],
      dtype='object')

In [47]:
for d in devoir_t2:
    conn.execute('''insert into devoir (name, trimestre, bareme ) values (?,?,?)''', (d, 2, notes.BAREME[d]))
conn.commit()

In [48]:
for e in eleves:
    c.execute('''select id from eleve where name=?''', (e,))
    e_id = c.fetchone()[0]
    for d in devoir_t2:
        c.execute('''select id from devoir where name=?''', (d,))
        d_id = c.fetchone()[0]
        conn.execute('''insert into note (valeur, eleve_id, devoir_id) values (?,?,?)''', (notes[e][d], e_id, d_id))
conn.commit()

# On essaie maintenant d'accéder à ces notes

Ce sont les deux dernières lignes de la requete qui permettent de lier les tables.

Requete pour un élève

In [73]:
c.execute(' '.join(['SELECT note.valeur, devoir.name',
              'FROM note, devoir, eleve',
              'WHERE eleve.name=?',
              'AND devoir.trimestre=?',
              'AND note.devoir_id=devoir.id',
              'AND note.eleve_id=eleve.id'
          ])
          , ("ABDOU Farida",2))
for i in c.fetchall():
    print(i)

(8.5, 'DS_15_11_27')
(12.0, 'DM_15_12_09')
(13.5, 'Boulettes')
(22.0, 'BB_16_01_23')
(12.0, 'DM_16_01_29')
(16.0, 'Brevet blanc Fevrier')
(11.5, 'Conn trimestre 2')


Requete pour tous les élèves

In [92]:
c.execute(' '.join(['SELECT eleve.name, devoir.name, note.valeur',
              'FROM note, devoir, eleve',
              'WHERE devoir.trimestre=?',
              'AND note.devoir_id=devoir.id',
              'AND note.eleve_id=eleve.id'
                   ])
          , (2,))
FORMAT = '%-6s\t\t%-10s\t\t\t\t%-8s'
print(FORMAT % ('Nom', 'Devoir', 'note'))
for i in c.fetchall():
    print(FORMAT % i)

Nom   		Devoir    				note    
ABDOU Farida		DS_15_11_27				8.5     
ABDOU Farida		DM_15_12_09				12.0    
ABDOU Farida		Boulettes 				13.5    
ABDOU Farida		BB_16_01_23				22.0    
ABDOU Farida		DM_16_01_29				12.0    
ABDOU Farida		Brevet blanc Fevrier				16.0    
ABDOU Farida		Conn trimestre 2				11.5    
ABOU BACAR Djaha		DS_15_11_27				7.0     
ABOU BACAR Djaha		DM_15_12_09				14.0    
ABOU BACAR Djaha		Boulettes 				14.5    
ABOU BACAR Djaha		BB_16_01_23				20.0    
ABOU BACAR Djaha		DM_16_01_29				16.5    
ABOU BACAR Djaha		Brevet blanc Fevrier				22.0    
ABOU BACAR Djaha		Conn trimestre 2				14.5    
AHAMADA Nabaouya		DS_15_11_27				10.5    
AHAMADA Nabaouya		DM_15_12_09				10.5    
AHAMADA Nabaouya		Boulettes 				14.5    
AHAMADA Nabaouya		BB_16_01_23				23.0    
AHAMADA Nabaouya		DM_16_01_29				14.5    
AHAMADA Nabaouya		Brevet blanc Fevrier				16.5    
AHAMADA Nabaouya		Conn trimestre 2				12.0    
AHAMADI Faina		DS_15_11_27				4.5     
AHAMADI Faina		DM_15_12_09				8.5    

Requete pour tous les élèves triée par devoir

In [95]:
c.execute(' '.join(['SELECT eleve.name, devoir.name, note.valeur',
              'FROM note, devoir, eleve',
              'WHERE devoir.trimestre=?',
              'AND note.devoir_id=devoir.id',
              'AND note.eleve_id=eleve.id',
              'ORDER BY devoir_id'
                   ])
          , (2,))
FORMAT = '%-6s\t\t%-10s\t\t\t\t%-8s'
print(FORMAT % ('Nom', 'Devoir', 'note'))
for i in c.fetchall():
    print(FORMAT % i)

Nom   		Devoir    				note    
ABDOU Farida		DS_15_11_27				8.5     
ABOU BACAR Djaha		DS_15_11_27				7.0     
AHAMADA Nabaouya		DS_15_11_27				10.5    
AHAMADI Faina		DS_15_11_27				4.5     
ALI Mardhuia		DS_15_11_27				12.5    
ALI SOULAIMANA Chamsia		DS_15_11_27				10.5    
ALSENE ALI MADI Stela		DS_15_11_27				8.5     
ANDRIATAHIANA Hoby		DS_15_11_27				16.0    
ANLI Emeline		DS_15_11_27				8.5     
ATHOUMANE Naouidat		DS_15_11_27				8.0     
BOUDRA Nassifanya		DS_15_11_27				10.5    
CHANFI Nadhrati		DS_15_11_27				4.5     
COMBO Moinécha		DS_15_11_27				17.0    
HALIDI Nisma		DS_15_11_27				12.0    
HAMZA Samianti		DS_15_11_27				7.0     
HOUMADI Mouslimati		DS_15_11_27				12.0    
HOUMADI Chaharazadi		DS_15_11_27				8.5     
HOUMADI Nasmi		DS_15_11_27				10.5    
HOUMADI Dhoirfia		DS_15_11_27				12.0    
LOUTOUFI Nachima		DS_15_11_27				8.0     
MALIDE El-Anzize		DS_15_11_27				12.0    
MONNE Kevin		DS_15_11_27				13.0    
MOUSSA Roibouanti		DS_15_11_27				16.0    
OUSSENI Hilma